<a href="https://colab.research.google.com/github/flrain2/Study/blob/main/naver_news_240420.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import os
import sys
import urllib.request
import platform
import calendar
import requests
import datetime
import time
import json
import re
import pandas as pd
from time import sleep
from bs4 import BeautifulSoup
from multiprocessing import Process
import csv

In [2]:
client_id = "ID"
client_secret = "PW"

title1 = []
pDate1 = []
description1 = []
org_link1 =[]
link1 = []
dt_now = datetime.datetime.now().strftime('%Y-%m-%d')

#[CODE 1]
def getRequestUrl(url):
    req = urllib.request.Request(url)
    req.add_header("X-Naver-Client-Id", client_id)
    req.add_header("X-Naver-Client-Secret", client_secret)

    try:
        response = urllib.request.urlopen(req)
        if response.getcode() == 200:
            print("[%s]Url Request Success" % datetime.datetime.now())
            return response.read().decode('utf-8')
    except Exception as e :
        print(e)
        print("[%s] Error for URL : %s" % (datetime.datetime.now(), url))
        return None

#[CODE 2]
def getNaverSearch(node, srcText, start, display):
    base = "https://openapi.naver.com/v1/search"
    node = "/%s.json" % node
    parameters = "?query=%s&start=%s&display=%s" % (urllib.parse.quote(srcText), start, display)

    url = base + node + parameters
    responseDecode = getRequestUrl(url)     #[CODE 1]

    if(responseDecode == None):
        return None
    else:
        return json.loads(responseDecode)

#[CODE 3]
def getPostData(post, jsonResult, cnt):
    cleanr = re.compile('<.*?>')

    title = post['title']
    titlec = re.sub(cleanr, '', title)
    description = post['description']
    descriptionc = re.sub(cleanr, '', description)
    org_link = post['originallink']
    link = post['link']

    pDate = datetime.datetime.strptime(post['pubDate'], '%a, %d %b %Y %H:%M:%S +0900')
    pDate = pDate.strftime('%Y-%m-%d %H:%M:%S')

    title1.append(titlec)
    description1.append(descriptionc)
    org_link1.append(org_link)
    link1.append(link)
    pDate1.append(pDate)

    jsonResult.append({'cnt':cnt, 'title':title, 'description':description,
                       'org_link':org_link, 'link':org_link, 'pDate':pDate})
    return

#[CODE 0]
def main():
    node = 'news'  #크롤링한 대상
    srcText = input('검색어를 입력하세요: ')
    cnt = 0
    jsonResult = []

    jsonResponse = getNaverSearch(node, srcText, 1, 100)  #[CODE 2]
    total = jsonResponse['total']

    while((jsonResponse != None) and (jsonResponse['display'] != 0)):
        for post in jsonResponse['items']:
            cnt+= 1
            getPostData(post, jsonResult, cnt)   #[CODE 3]

        start = jsonResponse['start'] + jsonResponse['display']
        jsonResponse = getNaverSearch(node, srcText, start, 100)   #[CODE 2]

    print('전체 검색 : %d 건' %total)

    #with open('%s_naver_%s.json' % (srcText, node), 'w', encoding='utf8') as outfile:
    #    jsonFile = json.dumps(jsonResult, indent=4, sort_keys = True, ensure_ascii = False)

    #    outfile.write(jsonFile)

    df=pd.DataFrame([title1, pDate1, description1, org_link1, link1 ]).T
    df.columns=['제목','날짜','내용','원래주소','네이버뉴스주소']

    print("가져온 데이터 : %d 건" %(cnt))
    #print('%s_naver_%s.json SAVED' % (srcText, node))

if __name__ == '__main__':
    main()


KeyboardInterrupt: Interrupted by user

In [ ]:
post_urls = link1

In [ ]:
# 데이터 클렌징
class ArticleParser(object):
    special_symbol = re.compile('[\{\}\[\]\/?,;:|\)*~`!^\-_+<>@\#$&▲▶◆◀■【】\\\=\(\'\"]')
    content_pattern = re.compile('본문 내용 | TV플레이어 | 동영상 뉴스 | flash 오류를 우회하기 위한 함수 추가function  flash removeCallback|tt | 앵커 멘트 | xa0')

    @classmethod
    def clear_content(cls, text):
        # 기사 본문에서 필요없는 특수문자 및 본문 양식 등을 다 지움
        newline_symbol_removed_text = text.replace('\\n', '').replace('\\t', '').replace('\\r', '') #줄바꿈, 탭, 커서를 앞의행으로 이동 제거
        special_symbol_removed_content = re.sub(cls.special_symbol, ' ', newline_symbol_removed_text) #특수문자 제거
        end_phrase_removed_content = re.sub(cls.content_pattern, '', special_symbol_removed_content) #일정 패턴 제거
        blank_removed_content = re.sub(' +', ' ', end_phrase_removed_content).lstrip()  # 공백 에러 삭제
        reversed_content = ''.join(reversed(blank_removed_content))  # 기사 내용을 reverse 한다.
        content = ''
        for i in range(0, len(blank_removed_content)):
            # reverse 된 기사 내용중, ".다"로 끝나는 경우 기사 내용이 끝난 것이기 때문에 기사 내용이 끝난 후의 광고, 기자 등의 정보는 다 지움
            if reversed_content[i:i + 2] == '.다':
                content = ''.join(reversed(reversed_content[i:]))
                break
        return content

    @classmethod
    def clear_headline(cls, text):
        # 기사 제목에서 필요없는 특수문자들을 지움
        newline_symbol_removed_text = text.replace('\\n', '').replace('\\t', '').replace('\\r', '')
        special_symbol_removed_headline = re.sub(cls.special_symbol, '', newline_symbol_removed_text)
        return special_symbol_removed_headline

In [ ]:
# 오류링크 제거
search = "sid=106"
for word in post_urls:
    if search in word:
        post_urls.remove(word)

search = "0004316027?sid=105"
for word in post_urls:
    if search in word:
        post_urls.remove(word)


In [ ]:
file_list = []
for content_url in post_urls:
  # 신문사 구분 link 뽑아내기
  title = content_url.split('/')[2]
  print(content_url)
  # 크롤링 대기 시간
  sleep(0.01)

#nnews naver
  if title == 'n.news.naver.com':
    request_content = requests.get(content_url)
    document_content = BeautifulSoup(request_content.content, 'html.parser')

    # 기사 제목 가져옴
    tag_headline = document_content.find_all('h2', {'id': 'title_area'})
    # 뉴스 기사 제목 초기화
    text_headline = ''
    text_headline = text_headline + ArticleParser.clear_headline(str(tag_headline[0].find_all(text=True)))
    print(text_headline)
    # 공백일 경우 기사 제외 처리
    if not text_headline:
        continue

    # 기사 본문 가져옴
    tag_content = document_content.find_all('div', {'id': 'contents'})
    # 뉴스 기사 본문 초기화
    text_sentence = ''
    text_sentence = text_sentence + ArticleParser.clear_content(str(tag_content[0].find_all(text=True)))
    print(text_sentence)
    # 공백일 경우 기사 제외 처리
    if not text_sentence:
        continue

    # 기사 언론사 가져옴
    tag_company = document_content.find_all('meta', {'property': 'og:article:author'})
    # 언론사 초기화
    text_company = ''
    text_company = text_company + str(tag_company[0].get('content'))
    print(text_company)
    # 공백일 경우 기사 제외 처리
    if not text_company:
        continue

    # data append to list
    data = [text_company, text_headline, text_sentence, content_url]
    file_list .append(data)

#인포멕스
  elif title == 'news.einfomax.co.kr':
    request_content = requests.get(content_url)
    document_content = BeautifulSoup(request_content.content, 'html.parser')

    # 기사 제목 가져옴
    tag_headline = document_content.find_all('h3', {'class': 'heading'})
    # 뉴스 기사 제목 초기화
    text_headline = ''
    text_headline = text_headline + ArticleParser.clear_headline(str(tag_headline[0].find_all(text=True)))
    print(text_headline)
    # 공백일 경우 기사 제외 처리
    if not text_headline:
        continue

    # 기사 본문 가져옴
    tag_content = document_content.find_all('article', {'id': 'article-view-content-div'})
    # 뉴스 기사 본문 초기화
    text_sentence = ''
    text_sentence = text_sentence + ArticleParser.clear_content(str(tag_content[0].find_all(text=True)))
    print(text_sentence)
    # 공백일 경우 기사 제외 처리
    if not text_sentence:
        continue

    # 기사 언론사 가져옴
    tag_company = document_content.find_all('meta', {'name': 'apple-mobile-web-app-title'})
    # 언론사 초기화
    text_company = ''
    text_company = text_company + str(tag_company[0].get('content'))
    print(text_company)
    # 공백일 경우 기사 제외 처리
    if not text_company:
        continue

    # data append to list
    data = [text_company, text_headline, text_sentence, content_url]
    file_list .append(data)

  else:
    pass

https://n.news.naver.com/mnews/article/050/0000073926?sid=101


<ipython-input-46-317c6cee7392>:18: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  text_headline = text_headline + ArticleParser.clear_headline(str(tag_headline[0].find_all(text=True)))
<ipython-input-46-317c6cee7392>:28: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  text_sentence = text_sentence + ArticleParser.clear_content(str(tag_content[0].find_all(text=True)))


선택의 고민을 풀어주는 큐레이션 전략박찬희의 경영 전략
경영전략 정보가 쏟아지고 볼 것이 넘쳐나는 시대 선택의 고민이 시작된다. 무엇을 사서 어떻게 할까 살피는 ‘행위적 결정’도 어렵지만 그 이전에 어떤 정보를 누구에게 얻을지 따져보는 ‘접촉과 노출의 결정’도 고민이다. 정보가 너무 많고 복잡해서 혼란스러울 때 의미 있는 정보를 가려서 제공하는 큐레이션 curation 의 가치가 부각된다. 큐레이션은 미술 전시 분야의 일로 많이 알려져 있다. 세상의 모든 미술작품을 볼 수는 없으니 전문적 안목을 가진 큐레이터가 일정한 테마에 맞춰서 작품을 선별해서 전시하고 관람을 돕는다. 미술 평론가는 이런 큐레이션의 타당성에 대해 평가하고 아울러 작가와 작품을 평가한다. 언론은 나름의 관점에서 보도하고 평론과 토론의 장을 제공한다. 이런 활동들은 미술작품의 시장 형성과 거래에 반영된다. 영화도 극장과 배급사가 일정한 큐레이션 역할을 한다. 유통사업도 상품을 가려서 추천하는 큐레이션 역할을 하는데 나름의 정체성과 고객 충성도를 가진 브랜드를 큐레이션의 대상으로 삼는 면도 있다. 이를테면 쇼핑몰은 입점 구조상 브랜드가 큐레이션의 중심이 되고 편집숍은 상품 구색을 맞춰 제공하는 기획자의 역할이 중심이 된다. 어디에 투자할지 망설이는 투자자들에게 테마에 맞게 포트폴리오를 짜주거나 펀드를 구성해서 끌어들이는 것도 비슷한 개념이다. 골라서 도와주는 큐레이션 인터넷과 모바일로 연결된 세상에서 더 넓은 범위에서 정보를 탐색하고 공유할 수 있다. 그런데 제한된 시간에 너무 많은 정보에 노출되면 이리저리 알아보고 선택하는 데 부담이 커진다. 특히 개인의 입장에선 여러 경로로 정보가 흩어져 쏟아지면 정신이 없다. 이른바 ‘부의 네트워크 효과 negative network externality ’인데 이때 정보 노출의 범위를 좁히고 탐색과 판단을 도와주면 사용자에 대한 접점을 장악하게 된다. 사용자 체험이 쌓여서 믿고 의지할 수 있게 되면 그 접점은 더욱 강화된다. 이것이 큐레이션의 역할이다. 

<ipython-input-46-317c6cee7392>:57: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  text_headline = text_headline + ArticleParser.clear_headline(str(tag_headline[0].find_all(text=True)))
<ipython-input-46-317c6cee7392>:67: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  text_sentence = text_sentence + ArticleParser.clear_content(str(tag_content[0].find_all(text=True)))


뉴욕마켓워치 위험 회피에 빅테크 집중 난타…채권↑달러↓주식 혼조
뉴욕 연합인포맥스 국제경제부 19일 이하 미국 동부시간 뉴욕 금융시장은 이스라엘이 이란에 군사적 보복을 감행했다는 소식에 안전 선호 심리가 강해졌다. 특히 고금리에 대한 우려까지 겹치면서 증시를 주도했던 빅테크 위주로 매물이 대거 쏟아졌다. 뉴욕증시는 이스라엘의 이란 공격에 따른 중동 위험과 함께 엔비디아를 비롯한 기술주들이 대거 조정을 받았지만 주요 주가지수는 혼조 양상을 보였다. 안전자산 선호 심리가 커지면서 주식시장에선 이른바 매그니피센트 7 M7 의 주가가 일제히 큰 폭으로 하락했다. 나스닥 지수는 2% 넘게 하락했고 스탠더드앤드푸어스 S P 500 지수는 5 000선이 무너졌다. 미국 국채가격은 상승 마감했다. 하지만 이스라엘이 이란을 직접 타격했다는 소식에 아시아장에서 급등했던 국채가격은 양측이 확전은 자제하는 움직임을 보이면서 상승폭을 줄였다. 미국 달러화 가치는 소폭 하락했다. 중동 사태에 대한 우려 속에 안전통화로 꼽히는 엔화가 달러보다 더 강세를 나타냈다. 다만 뉴욕증시가 대형 기술주를 중심으로 장중 낙폭을 확대하면서 위험회피 분위기가 짙어지자 달러는 반등하는 움직임을 보였다. 주요 6개 통화에 대한 달러화 가치를 반영하는 달러인덱스는 결국 약보합권까지 낙폭을 축소했다. 뉴욕 유가는 상승했다. 이스라엘이 이란에 대한 보복을 위해 본토 공격에 나서면서 지정학적 위험이 불거졌다. 그러나 두 나라의 갈등이 원유 공급을 저해할 정도의 중동 전쟁으로 확산되지는 않을 것이라는 전망에 유가 상승폭은 제한됐다. 이스라엘과 이란의 군사 충돌로 안전 선호 심리가 강해졌다. 특히 뉴욕 증시에서 빅테크는 집중적으로 난타 당했다. 주가가 가장 크게 흔들린 주식은 엔비디아였다. 작년 11월부터 시작된 증시 랠리의 중심에서 인공지능 AI 열풍이 있었고 엔비디아는 그 중에서도 핵심 기업이었다. 하지만 주가 상승세가 과도했다는 인식이 터져나온듯 위험 회피 심리가 강해지자 집중 매도 대상이 됐다. 엔비디아는 이

In [ ]:
from pandas import DataFrame

#list to dataframe
df = DataFrame (file_list,columns=['text_company','text_headline','text_sentence','content_url'])
df

text_company                                    text_headline  \
0    한경비즈니스 | 네이버                   선택의 고민을 풀어주는 큐레이션 전략박찬희의 경영 전략   
1      매일경제 | 네이버  1위 독주하다 넘어진 혁신 아이콘…‘비장의 무기’ 개발 착수했다는데 박민기의 월드버스   
2      매일경제 | 네이버   아이언맨 ‘자비스’ 진짜 내년에 나온다고…머스크형 장담 믿어도 될까 홍키자의 빅테크   
3     헤럴드경제 | 네이버                      구글 이스라엘 서비스 반대 시위 직원 28명 해고   
4          연합인포맥스              뉴욕마켓워치 위험 회피에 빅테크 집중 난타…채권↑달러↓주식 혼조   
..            ...                                              ...   
516  지디넷코리아 | 네이버              인공지능이 대세...국내 SW·SI 기업 AI 전문가 전진 배치   
517    이데일리 | 네이버                    딥세일즈 데이터바우처 활용 위한 데이터셋 30종 공개   
518  한국경제TV | 네이버      툰스퀘어 AWS와 협업…글로벌 무대에서 ‘이미지 생성AI 자동화 방법론’ 강연   
519     뉴스1 | 네이버                      지금 매수해 10년간 보유해야 할 AI 주식 2선   
520     뉴스1 | 네이버                    엔비디아가 투자한 사운드하운드 한 달간 300% 폭등   

                                         text_sentence  \
0    경영전략 정보가 쏟아지고 볼 것이 넘쳐나는 시대 선택의 고민이 시작된다. 무엇을 사...   
1    애플 전기차 철수…혼합현실 성적 부진 인류 도와줄 ‘가정용 로봇’ 개발 착수 타 기...   
2    “내년 또는 2026년에는 인간보다 더 똑똑한 인공지능 AI 이 개발될 것이다.” ...   
3    클라우드컴퓨팅·AI 서비스 제공 중단 요구 시위 지난달엔 이스라엘 관련 행사서 항의...   
4    뉴욕 연합인포맥스 국제경제부 19일 이하 미국 동부시간 뉴욕 금융시장은 이스라엘이 ...   
..                                                 ...   
516  올해 AI 산업 확대 원년...AI 미래먹거리 낙점하고 사업 성과에 사활 국내 IT...   
517  바이어·투자사 정보 등 기업 필수 데이터 총 350만개 레코드로 기업 효율성 지원 ...   
518  AWS Innovate Conference 툰스퀘어의 기술력·경험 공유 생성형 AI...   
519  스마트폰 화면에 뜬 엔비디아 로고. ⓒ 로이터 뉴스1 ⓒ News1 박형기 기자 서...   
520  미국 음성 인식 전문 AI 업체 사운드하운드 로고 ⓒ 로이터 뉴스1 ⓒ News1 ...   

                                           content_url  
0    https://n.news.naver.com/mnews/article/050/000...  
1    https://n.news.naver.com/mnews/article/009/000...  
2    https://n.news.naver.com/mnews/article/009/000...  
3    https://n.news.naver.com/mnews/article/016/000...  
4    https://news.einfomax.co.kr/news/articleView.h...  
..                                                 ...  
516  https://n.news.naver.com/mnews/article/092/000...  
517  https://n.news.naver.com/mnews/article/018/000...  
518  https://n.news.naver.com/mnews/article/215/000...  
519  https://n.news.naver.com/mnews/article/421/000...  
520  https://n.news.naver.com/mnews/article/421/000...  

[521 rows x 4 columns]

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import csv
#df.to_csv('/content/drive/MyDrive/Colab Notebooks/MS_craw.csv')
#df.to_csv('/content/drive/MyDrive/Colab Notebooks/apple_craw.csv')
#df.to_csv('/content/drive/MyDrive/Colab Notebooks/aramco_craw.csv')
#df.to_csv('/content/drive/MyDrive/Colab Notebooks/envidia_craw.csv')
df.to_csv('/content/drive/MyDrive/Colab Notebooks/amazon_craw.csv')
